In [38]:
#Import the libraries we need
from   fredapi  import Fred
import pandas   as pd
import numpy    as np
import time

In [25]:
#Read in the scaling values
z_scores = pd.read_csv("FRED EURUSD D1 scale factors.csv")

In [2]:
#Define important variables
fred_api                = "9e9bb88305722ec47066c843944bf55f"
fred_broad_dollar_index = "DTWEXBGS"
fred_us_10y             = "DGS10"
fred_us_5y_inflation    = "T5YIFR"

In [3]:
#Fetch the data we need
#Login to fred
fred = Fred(api_key=fred_api)

In [4]:
#Fetch the data
dollar_index    = fred.get_series(fred_broad_dollar_index)
us_10y          = fred.get_series(fred_us_10y)
us_5y_inflation = fred.get_series(fred_us_5y_inflation)

In [40]:
#Name the series so we can merge the data
dollar_index.name    =  "Dollar Index"
us_10y.name          =  "Bond Interest"
us_5y_inflation.name =  "Inflation"

In [39]:
def fetch_fred_data():
    #Merge the data
    merged_data = pd.merge(dollar_index,us_10y,left_index=True,right_index=True)
    merged_data = merged_data.merge(us_5y_inflation,left_index=True,right_index=True)
    #Fill in missing values
    merged_data.fillna(merged_data.rolling(window=5,min_periods=1).mean(),inplace=True)
    #Fetch the most recent data
    merged_data = merged_data.iloc[-1,:]
    #Scale the data
    for i in np.arange(0,3):
        merged_data.iloc[i] = ((merged_data[i] - z_scores.iloc[0,i+6]) / z_scores.iloc[1,i+6])
    #Write out our scaled data
    merged_data.to_csv("/home/volatily/.wine/drive_c/Program Files/MetaTrader 5/MQL5/Files/FRED EURUSD ALT DATA.csv")

In [ ]:
while True:
        #Update the fred data for our MT5 EA
        fetch_fred_data
        #If we have finished all checks then we can wait for one day before checking for new data
        time.sleep(24 * 60 * 60)